In [102]:
import os

def load_emails(folder_path, label):
    emails = []
    for filename in os.listdir(folder_path):
        file_path = os.path.join(folder_path, filename)
        if os.path.isfile(file_path): 
            with open(file_path, 'r', encoding='latin1') as file:
                content = file.read()
                emails.append((content, label))

    return emails

ham_emails_1 = load_emails('dataset/easy_ham', label=0)
spam_emails_1 = load_emails('dataset/spam', label=1)
ham_emails_2 = load_emails('dataset/easy_ham2', label=0)
spam_emails_2 = load_emails('dataset/spam1', label=1)
ham_emails_3 = load_emails('dataset/easy_ham_3', label=0)
spam_emails_3 = load_emails('dataset/spam_2', label=1)
ham_emails_4 = load_emails('dataset/hard_ham', label=0)
spam_emails_4 = load_emails('dataset/spam3', label=1)

ham_emails = ham_emails_1 + ham_emails_2 + ham_emails_3 + ham_emails_4
spam_emails = spam_emails_1 + spam_emails_2 + spam_emails_3 + spam_emails_4
all_emails = ham_emails + spam_emails

print(f'Ham emails: {len(ham_emails)}')
print(f'Spam emails: {len(spam_emails)}')
print(f'Total emails loaded: {len(all_emails)}')


Ham emails: 6703
Spam emails: 3797
Total emails loaded: 10500


In [103]:
all_emails

[('From exmh-workers-admin@redhat.com  Thu Aug 22 12:36:23 2002\nReturn-Path: <exmh-workers-admin@example.com>\nDelivered-To: zzzz@localhost.netnoteinc.com\nReceived: from localhost (localhost [127.0.0.1])\n\tby phobos.labs.netnoteinc.com (Postfix) with ESMTP id D03E543C36\n\tfor <zzzz@localhost>; Thu, 22 Aug 2002 07:36:16 -0400 (EDT)\nReceived: from phobos [127.0.0.1]\n\tby localhost with IMAP (fetchmail-5.9.0)\n\tfor zzzz@localhost (single-drop); Thu, 22 Aug 2002 12:36:16 +0100 (IST)\nReceived: from listman.example.com (listman.example.com [66.187.233.211]) by\n    dogma.slashnull.org (8.11.6/8.11.6) with ESMTP id g7MBYrZ04811 for\n    <zzzz-exmh@example.com>; Thu, 22 Aug 2002 12:34:53 +0100\nReceived: from listman.example.com (localhost.localdomain [127.0.0.1]) by\n    listman.redhat.com (Postfix) with ESMTP id 8386540858; Thu, 22 Aug 2002\n    07:35:02 -0400 (EDT)\nDelivered-To: exmh-workers@listman.example.com\nReceived: from int-mx1.corp.example.com (int-mx1.corp.example.com\n   

In [104]:
!pip install pandas

In [105]:
import sys
print(sys.executable)

!{sys.executable} -m pip install pandas

c:\Users\Admin\AppData\Local\Programs\Python\Python312\python.exe



[notice] A new release of pip is available: 24.0 -> 25.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [106]:
import pandas as pd

emails = pd.DataFrame(all_emails, columns=["email_text", "label"])
print(emails.head())

                                          email_text  label
0  From exmh-workers-admin@redhat.com  Thu Aug 22...      0
1  From Steve_Burt@cursor-system.com  Thu Aug 22 ...      0
2  From timc@2ubh.com  Thu Aug 22 13:52:59 2002\n...      0
3  From irregulars-admin@tb.tf  Thu Aug 22 14:23:...      0
4  From exmh-users-admin@redhat.com  Thu Aug 22 1...      0


In [107]:
import sys
!{sys.executable} -m pip install scikit-learn


[notice] A new release of pip is available: 24.0 -> 25.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [108]:
emails = emails.dropna()

In [109]:
from sklearn.model_selection import train_test_split

X = emails['email_text']
y = emails['label']

X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42, stratify=y
)

In [110]:
print(len(X_train))
print(len(y_train))

8400
8400


In [111]:
len(X_train)

8400

In [112]:
X_train = X_train.str.lower()

In [113]:
print(len(X_train))
print(len(y_train))

8400
8400


In [114]:
emails.head()

email_text  label
0  From exmh-workers-admin@redhat.com  Thu Aug 22...      0
1  From Steve_Burt@cursor-system.com  Thu Aug 22 ...      0
2  From timc@2ubh.com  Thu Aug 22 13:52:59 2002\n...      0
3  From irregulars-admin@tb.tf  Thu Aug 22 14:23:...      0
4  From exmh-users-admin@redhat.com  Thu Aug 22 1...      0

In [115]:
print(type(X_train))

<class 'pandas.core.series.Series'>


In [116]:
import re

X_train = X_train.apply(lambda x: re.sub(r'[^a-zA-Z\s]', '', str(x)).lower())

In [117]:
from sklearn.feature_extraction.text import CountVectorizer

vectorizer = CountVectorizer(stop_words='english')
X_train_vec = vectorizer.fit_transform(X_train)

In [118]:
from sklearn.ensemble import RandomForestClassifier

random_classify = RandomForestClassifier(random_state=42)
random_classify.fit(X_train_vec,y_train)


RandomForestClassifier(random_state=42)

In [119]:
from sklearn.model_selection import cross_val_score

scores = cross_val_score(random_classify, X_train_vec, y_train, cv=3, scoring='accuracy')
scores

array([0.98678571, 0.98714286, 0.9925    ])

In [120]:
from sklearn.naive_bayes import MultinomialNB

naive = MultinomialNB()
naive.fit(X_train_vec,y_train)

MultinomialNB()

In [121]:
y_pred = naive.predict(X_train_vec)

In [122]:
from sklearn.model_selection import cross_val_score

scores = cross_val_score(naive, X_train_vec, y_train, cv=3, scoring='accuracy')
scores

array([0.97285714, 0.98107143, 0.97428571])

In [123]:
from sklearn.feature_extraction.text import CountVectorizer

bow_vectorizer = CountVectorizer(stop_words='english')
X_train_bow = bow_vectorizer.fit_transform(X_train)

In [124]:
from sklearn.ensemble import RandomForestClassifier

random_classify = RandomForestClassifier(random_state=42)
random_classify.fit(X_train_bow,y_train)

RandomForestClassifier(random_state=42)

In [125]:
scores = cross_val_score(random_classify, X_train_bow, y_train, cv=3, scoring='accuracy')
scores

array([0.98678571, 0.98714286, 0.9925    ])

In [126]:
naive_bow = MultinomialNB()
naive_bow.fit(X_train_bow,y_train)

MultinomialNB()

In [127]:
scores = cross_val_score(naive_bow, X_train_bow, y_train, cv=3, scoring='accuracy')
scores

array([0.97285714, 0.98107143, 0.97428571])

In [128]:
from sklearn.feature_extraction.text import TfidfVectorizer

tfidf_vectorizer = TfidfVectorizer(stop_words='english')
X_train_tfidf = tfidf_vectorizer.fit_transform(X_train)

In [129]:
naive_tf = MultinomialNB()
naive_tf.fit(X_train_bow,y_train)

MultinomialNB()

In [130]:
scores = cross_val_score(naive_bow, X_train_bow, y_train, cv=3, scoring='accuracy')
scores

array([0.97285714, 0.98107143, 0.97428571])

In [131]:
import re
import pandas as pd
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.ensemble import RandomForestClassifier
from sklearn.pipeline import Pipeline

class TextPreprocessor(BaseEstimator, TransformerMixin):
    def fit(self, X, y=None):
        return self
    
    def transform(self, X, y=None):
        return X.apply(lambda x: re.sub(r'[^a-zA-Z\s]', '', str(x)).lower())

spam_pipeline = Pipeline([
    ('preprocessor', TextPreprocessor()),                  
    ('vectorizer', CountVectorizer(stop_words='english')), 
    ('classifier', RandomForestClassifier(random_state=42))
])

spam_pipeline.fit(X_train, y_train)

y_pred = spam_pipeline.predict(X_test)


In [132]:
from sklearn.metrics import accuracy_score
print("Test Accuracy:", accuracy_score(y_test, y_pred))

Test Accuracy: 0.9947619047619047
